In [1]:
!python -V

Python 3.9.19


In [2]:
import pandas as pd

In [3]:
import pickle

In [4]:
import seaborn as sns
import matplotlib.pyplot as plt

In [27]:
from sklearn.feature_extraction import DictVectorizer
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Lasso
from sklearn.linear_model import Ridge

from sklearn.metrics import root_mean_squared_error

In [6]:
import mlflow


mlflow.set_tracking_uri("sqlite:///mlflow.db")
mlflow.set_experiment("nyc-taxi-experiment")

<Experiment: artifact_location='./mlruns/1', creation_time=1716730384713, experiment_id='1', last_update_time=1716730384713, lifecycle_stage='active', name='nyc-taxi-experiment', tags={}>

In [11]:
def read_dataframe(filename):
    if filename.endswith('.csv'):
        df = pd.read_csv(filename)

        df.lpep_dropoff_datetime = pd.to_datetime(df.lpep_dropoff_datetime)
        df.lpep_pickup_datetime = pd.to_datetime(df.lpep_pickup_datetime)
    elif filename.endswith('.parquet'):
        df = pd.read_parquet(filename)

    df['duration'] = df.lpep_dropoff_datetime - df.lpep_pickup_datetime
    df.duration = df.duration.apply(lambda td: td.total_seconds() / 60)

    df = df[(df.duration >= 1) & (df.duration <= 60)]

    categorical = ['PULocationID', 'DOLocationID']
    df[categorical] = df[categorical].astype(str)
    
    return df

In [14]:
df_train = read_dataframe('../data/green_tripdata_2023-01.parquet')
df_val = read_dataframe('../data/green_tripdata_2023-02.parquet')

In [15]:
len(df_train), len(df_val)

(65946, 62574)

In [16]:
df_train['PU_DO'] = df_train['PULocationID'] + '_' + df_train['DOLocationID']
df_val['PU_DO'] = df_val['PULocationID'] + '_' + df_val['DOLocationID']

In [17]:
categorical = ['PU_DO'] #'PULocationID', 'DOLocationID']
numerical = ['trip_distance']

dv = DictVectorizer()

train_dicts = df_train[categorical + numerical].to_dict(orient='records')
X_train = dv.fit_transform(train_dicts)

val_dicts = df_val[categorical + numerical].to_dict(orient='records')
X_val = dv.transform(val_dicts)

In [18]:
target = 'duration'
y_train = df_train[target].values
y_val = df_val[target].values

In [19]:
lr = LinearRegression()
lr.fit(X_train, y_train)

y_pred = lr.predict(X_val)

mean_squared_error(y_val, y_pred, squared=False)

/home/kristina/anaconda3/envs/experiment-tracking-env/lib/python3.9/site-packages/sklearn/metrics/_regression.py:492: FutureWarning: 'squared' is deprecated in version 1.4 and will be removed in 1.6. To calculate the root mean squared error, use the function'root_mean_squared_error'.
  warnings.warn(


6.037713760833734

In [23]:
with open('../models/lin_reg.bin', 'wb') as f_out:
    pickle.dump((dv, lr), f_out)

In [28]:
with mlflow.start_run():

    mlflow.set_tag("developer", "Kristina")

    mlflow.log_param("train-data-path", "../data/green_tripdata_2023-01.parquet")
    mlflow.log_param("valid-data-path", "../data/green_tripdata_2023-02.parquet")

    alpha = 0.1
    mlflow.log_param("alpha", alpha)
    lr = Lasso(alpha)
    lr.fit(X_train, y_train)

    y_pred = lr.predict(X_val)
    rmse = root_mean_squared_error(y_val, y_pred)
    mlflow.log_metric("rmse", rmse)

    mlflow.log_artifact(local_path="../models/lin_reg.bin", artifact_path="models_pickle")

In [29]:
import xgboost as xgb

In [30]:
from hyperopt import fmin, tpe, hp, STATUS_OK, Trials
from hyperopt.pyll import scope

In [31]:
train = xgb.DMatrix(X_train, label=y_train)
valid = xgb.DMatrix(X_val, label=y_val)

In [32]:
def objective(params):
    with mlflow.start_run():
        mlflow.set_tag("model", "xgboost")
        mlflow.log_params(params)
        booster = xgb.train(
            params=params,
            dtrain=train,
            num_boost_round=1000,
            evals=[(valid, 'validation')],
            early_stopping_rounds=50
        )
        y_pred = booster.predict(valid)
        rmse = root_mean_squared_error(y_val, y_pred)
        mlflow.log_metric("rmse", rmse)

    return {'loss': rmse, 'status': STATUS_OK}

In [33]:
search_space = {
    'max_depth': scope.int(hp.quniform('max_depth', 4, 100, 1)),
    'learning_rate': hp.loguniform('learning_rate', -3, 0),
    'reg_alpha': hp.loguniform('reg_alpha', -5, -1),
    'reg_lambda': hp.loguniform('reg_lambda', -6, -1),
    'min_child_weight': hp.loguniform('min_child_weight', -1, 3),
    'objective': 'reg:linear',
    'seed': 42
}

best_result = fmin(
    fn=objective,
    space=search_space,
    algo=tpe.suggest,
    max_evals=50,
    trials=Trials()
)

  0%|                                                                                                                                                                                        | 0/50 [00:00<?, ?trial/s, best loss=?]

/home/kristina/anaconda3/envs/experiment-tracking-env/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [22:07:20] WARNING: /workspace/src/objective/regression_obj.cu:209: reg:linear is now deprecated in favor of reg:squarederror.
  warnings.warn(smsg, UserWarning)



[0]	validation-rmse:7.71044                                                                                                                                                                                                         
[1]	validation-rmse:6.69058                                                                                                                                                                                                         
[2]	validation-rmse:6.07817                                                                                                                                                                                                         
[3]	validation-rmse:5.71283                                                                                                                                                                                                         
[4]	validation-rmse:5.51031                                                         

/home/kristina/anaconda3/envs/experiment-tracking-env/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [22:07:39] WARNING: /workspace/src/objective/regression_obj.cu:209: reg:linear is now deprecated in favor of reg:squarederror.
  warnings.warn(smsg, UserWarning)



[0]	validation-rmse:8.41379                                                                                                                                                                                                         
[1]	validation-rmse:7.68948                                                                                                                                                                                                         
[2]	validation-rmse:7.12053                                                                                                                                                                                                         
[3]	validation-rmse:6.67869                                                                                                                                                                                                         
[4]	validation-rmse:6.33899                                                         

...

[0]	validation-rmse:6.66564                                                                                                                                                                                                         
[1]	validation-rmse:5.79998                                                                                                                                                                                                         
[2]	validation-rmse:5.54797                                                                                                                                                                                                         
[3]	validation-rmse:5.45760                                                                                                                                                                                                         
[4]	validation-rmse:5.41265                                                         

/home/kristina/anaconda3/envs/experiment-tracking-env/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [23:08:24] WARNING: /workspace/src/objective/regression_obj.cu:209: reg:linear is now deprecated in favor of reg:squarederror.
  warnings.warn(smsg, UserWarning)



[0]	validation-rmse:7.99984                                                                                                                                                                                                         
[1]	validation-rmse:7.07363                                                                                                                                                                                                         
[2]	validation-rmse:6.43223                                                                                                                                                                                                         
[3]	validation-rmse:6.00390                                                                                                                                                                                                         
[4]	validation-rmse:5.71704                                                         

/home/kristina/anaconda3/envs/experiment-tracking-env/lib/python3.9/site-packages/xgboost/core.py:160: UserWarning: [23:08:52] WARNING: /workspace/src/objective/regression_obj.cu:209: reg:linear is now deprecated in favor of reg:squarederror.
  warnings.warn(smsg, UserWarning)



[0]	validation-rmse:8.48320                                                                                                                                                                                                         
[1]	validation-rmse:7.80593                                                                                                                                                                                                         
[2]	validation-rmse:7.26440                                                                                                                                                                                                         
[3]	validation-rmse:6.83673                                                                                                                                                                                                         
[4]	validation-rmse:6.50020                                                         

In [35]:
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, ExtraTreesRegressor
from sklearn.svm import LinearSVR

mlflow.sklearn.autolog()

for model_class in (RandomForestRegressor, GradientBoostingRegressor, ExtraTreesRegressor, LinearSVR):

    with mlflow.start_run():

        mlflow.log_param("train-data-path", "../data/green_tripdata_2023-01.parquet")
        mlflow.log_param("valid-data-path", "../data/green_tripdata_2023-02.parquet")
        mlflow.log_artifact(local_path="../models/preprocessor.b", artifact_path="preprocessor")

        mlmodel = model_class()
        mlmodel.fit(X_train, y_train)

        y_pred = mlmodel.predict(X_val)
        rmse = root_mean_squared_error(y_val, y_pred)
        mlflow.log_metric("rmse", rmse)
        

2024/05/27 09:12:35 WARNING mlflow.utils.autologging_utils: You are using an unsupported version of sklearn. If you encounter errors during autologging, try upgrading / downgrading sklearn to a supported version, or try upgrading MLflow.


FileNotFoundError: [Errno 2] No such file or directory: '../models/preprocessor.b'